In [ ]:
import pymysql
import pandas as pd
from dotenv import load_dotenv
import os

load_dotenv()

# MySQL 연결
conn = pymysql.connect(
    host=os.getenv("DB_HOST"),
    user=os.getenv("DB_USER"),
    password=os.getenv("DB_PASSWORD"),
    db=os.getenv("DB_NAME"),
    charset='utf8mb4'
)

# 구별 점포 수 CSV
query_shop_count_by_gu = """SELECT ca.gu AS 구,
       sca.name AS 업종명,
       SUM(s.shop_count) AS 점포수
FROM Shop_Count s
JOIN Commercial_Area ca ON s.commercial_area_code = ca.code
JOIN Service_Category sca ON s.service_category_code = sca.code
WHERE sca.name IN ('한식음식점','중식음식점','일식음식점','양식음식점',
                   '제과점','패스트푸드점','치킨전문점','분식전문점',
                   '호프-간이주점','커피-음료')
GROUP BY ca.gu, sca.name
ORDER BY ca.gu, 점포수 DESC;"""
df_shop_count_by_gu = pd.read_sql(query_shop_count_by_gu, conn)
df_shop_count_by_gu.to_csv('./src/eda/shop_count_by_gu.csv', index=False, encoding='utf-8-sig')

# 동별 점포 수 CSV
query_shop_count_by_dong = """SELECT ca.gu AS 구,
       ca.dong AS 동,
       sca.name AS 업종명,
       SUM(s.shop_count) AS 점포수
FROM Shop_Count s
JOIN Commercial_Area ca ON s.commercial_area_code = ca.code
JOIN Service_Category sca ON s.service_category_code = sca.code
WHERE sca.name IN ('한식음식점','중식음식점','일식음식점','양식음식점',
                   '제과점','패스트푸드점','치킨전문점','분식전문점',
                   '호프-간이주점','커피-음료')
GROUP BY ca.gu, ca.dong, sca.name
ORDER BY ca.gu, ca.dong, 점포수 DESC;"""
df_shop_count_by_dong = pd.read_sql(query_shop_count_by_dong, conn)
df_shop_count_by_dong.to_csv('./src/eda/shop_count_by_dong.csv', index=False, encoding='utf-8-sig')

# 상권별 점포 수 CSV
query_shop_count_by_area = """SELECT ca.gu AS 구,
       ca.name AS 상권명,
       sca.name AS 업종명,
       SUM(s.shop_count) AS 점포수
FROM Shop_Count s
JOIN Commercial_Area ca ON s.commercial_area_code = ca.code
JOIN Service_Category sca ON s.service_category_code = sca.code
WHERE sca.name IN ('한식음식점','중식음식점','일식음식점','양식음식점',
                   '제과점','패스트푸드점','치킨전문점','분식전문점',
                   '호프-간이주점','커피-음료')
GROUP BY ca.gu, ca.name, sca.name
ORDER BY ca.gu, 점포수 DESC;"""
df_shop_count_by_area = pd.read_sql(query_shop_count_by_area, conn)
df_shop_count_by_area.to_csv('./src/eda/shop_count_by_area.csv', index=False, encoding='utf-8-sig')

conn.close()

/tmp/ipykernel_8355/1264956762.py:25: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_gu = pd.read_sql(query_gu, conn)
/tmp/ipykernel_8355/1264956762.py:41: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_dong = pd.read_sql(query_dong, conn)
/tmp/ipykernel_8355/1264956762.py:57: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_area = pd.read_sql(query_area, conn)


## 구/동/상권별 CSV 파일 불러오기

In [ ]:
import pandas as pd

# 구/동/상권별 CSV
df_shop_count_by_gu = pd.read_csv('./src/eda/shop_count_by_gu.csv', encoding='utf-8-sig')
df_shop_count_by_dong = pd.read_csv('./src/eda/shop_count_by_dong.csv', encoding='utf-8-sig')
df_shop_count_by_area = pd.read_csv('./src/eda/shop_count_by_area.csv', encoding='utf-8-sig')

In [ ]:
# 한 셀에서 여러 개 확인 display
display(df_shop_count_by_gu.head())
display(df_shop_count_by_dong.head())
display(df_shop_count_by_area.head())

구      업종명      점포수
0  강남구    한식음식점  15458.0
1  강남구    커피-음료   7013.0
2  강남구    양식음식점   4656.0
3  강남구  호프-간이주점   4161.0
4  강남구    일식음식점   3292.0

구     동      업종명    점포수
0  강남구  개포2동    한식음식점  179.0
1  강남구  개포2동    커피-음료   37.0
2  강남구  개포2동    분식전문점   36.0
3  강남구  개포2동  호프-간이주점   32.0
4  강남구  개포2동    일식음식점   23.0

구     상권명    업종명     점포수
0  강남구     역삼역  한식음식점  1397.0
1  강남구     선릉역  한식음식점  1011.0
2  강남구    신논현역  한식음식점   944.0
3  강남구  포스코사거리  한식음식점   702.0
4  강남구   뱅뱅사거리  한식음식점   636.0

#### 구별 업종 점포수 시각화

In [ ]:
import plotly.express as px

fig_shop_count_by_gu = px.bar(df_shop_count_by_gu,
                x='구',
                y='점포수',
                color='업종명',
                text='점포수',
                title='구별 10개 업종 점포 수',
                barmode='group')
fig_shop_count_by_gu.update_layout(xaxis_title='구', yaxis_title='점포 수', legend_title='업종')
fig_shop_count_by_gu.show()

#### 동별 업종 점포수 시각화

In [ ]:
fig_shop_count_by_dong = px.treemap(df_shop_count_by_dong,
                      path=['구', '동', '업종명'],
                      values='점포수',
                      color='점포수',
                      color_continuous_scale='Blues',
                      title='동별 10개 업종 점포 수')
fig_shop_count_by_dong.show()

### 상권별 업종 점포수 시각화

#### 전체 상권별 점포수

In [ ]:
fig_shop_count_by_area = px.bar(df_shop_count_by_area,
                  x='상권명',
                  y='점포수',
                  color='업종명',
                  title='상권별 업종 분포',
                  text='점포수')
fig_shop_count_by_area.update_layout(xaxis_title='상권', yaxis_title='점포 수', legend_title='업종', height=600)
fig_shop_count_by_area.show()

#### 점포수 상위 20개 상권

In [ ]:
import pandas as pd 
import plotly.express as px

# 상위 20개 상권 추출 (총 점포수 기준)
top_shop_count_n = df_shop_count_by_area.groupby('상권명')['점포수'].sum().sort_values(ascending=False).head(20)
top_order = top_shop_count_n.index  # 순서 정보 저장

# 상위 20개 상권 필터링 후 색상별 합계를 피벗
df_top = df_shop_count_by_area[df_shop_count_by_area['상권명'].isin(top_order)].copy()
df_pivot = df_top.pivot_table(index='상권명', columns='업종명', values='점포수', aggfunc='sum').fillna(0)

# x축 순서 강제
df_pivot = df_pivot.loc[top_order]

# 다시 long format으로 변환
df_long = df_pivot.reset_index().melt(id_vars='상권명', var_name='업종명', value_name='점포수')

# 시각화
fig = px.bar(df_long,
             x='상권명',
             y='점포수',
             color='업종명',
             title='점포 수 상위 20개 상권 (업종별)',
             text='점포수')

fig.update_layout(xaxis_title='상권', yaxis_title='점포 수', legend_title='업종', height=600)
fig.show()

In [ ]:
import plotly_express as px

top_n = df_shop_count_by_area.groupby('상권명')['점포수'].sum().sort_values(ascending=False).head(20).index
df_top = df_shop_count_by_area[df_shop_count_by_area['상권명'].isin(top_n)].copy()

# x축 순서 지정 (점포 순)
df_top.loc[:, '상권명'] = pd.Categorical(
    df_top['상권명'],
    categories=df_top.groupby('상권명')['점포수'].sum()
                     .sort_values(ascending=False).index,
    ordered=True
)
fig_top = px.bar(df_top,
                 x='상권명',
                 y='점포수',
                 color='업종명',
                 title='점포 수 상위 20개 상권 (업종별)',
                 text='점포수')
fig_top.update_layout(xaxis_title='상권', yaxis_title='점포 수', legend_title='업종', height=600)
fig_top.show()

## 상권별 점포 수 + 면적 조회 CSV 파일 저장

### 밀도(면적, 점포수 활용) 비교 csv 파일 불러오기

In [ ]:
import pymysql
import pandas as pd

# MySQL 연결
conn = pymysql.connect(
    host=os.getenv("DB_HOST"),
    user=os.getenv("DB_USER"),
    password=os.getenv("DB_PASSWORD"),
    db=os.getenv("DB_NAME"),
    charset='utf8mb4'
)

query_density = """SELECT ca.gu AS 구,
       ca.dong AS 동,
       ca.name AS 상권명,
       ca.area_size AS 면적,
       SUM(s.shop_count) AS 점포수,
       SUM(s.shop_count)/ca.area_size AS 점포밀도
       FROM Shop_Count s
       JOIN Commercial_Area ca ON s.commercial_area_code = ca.code
       GROUP BY ca.gu, ca.dong, ca.name, ca.area_size
       ORDER BY 점포밀도 DESC;"""
df_density = pd.read_sql(query_density, conn)
df_density.to_csv('./src/eda/commercial_area_density.csv', index=False, encoding='utf-8-sig')

conn.close()

/tmp/ipykernel_8355/3484900918.py:23: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



## Choropleth 맵 시각화

#### 구 단위 시각화

/home/hyubi/dev_ws/eda_project/eda-repo-4


#### 행정동 단위 시각화

In [ ]:
import pandas as pd
import numpy as np
import plotly.express as px

#  GeoJSON 불러오기
with open('./src/eda/hangjeongdong_서울특별시.geojson', 'r', encoding='utf-8') as f:
    geo_dong = json.load(f)

# GeoJSON에서 동 이름만 추출 (adm_nm -> 동 이름)
for feature in geo_dong['features']:
    # 예: "서울특별시 종로구 사직동" -> "사직동"
    feature['properties']['dong_name'] = feature['properties']['adm_nm'].split()[-1]

#  동 단위 Choropleth 그리기
fig = px.choropleth(
    df_density,
    geojson=geo_dong,
    featureidkey='properties.dong_name',
    locations='동',
    color='점포밀도',
    color_continuous_scale='Reds',
    range_color=(0, 0.07),          # 색상 범위 지정하면 더 차이를 자세하게 볼 수 있음, 현재 기준은 중랑구 신아타운 점포밀도/2
    hover_data=['구', '상권명', '점포밀도'],
    title='서울 동별 상권 점포 밀도 (범위 제한)'
)
#  지도 범위 자동 맞춤, 배경 제거
fig.update_geos(fitbounds="locations", visible=False)

#  출력
fig.show()

In [74]:
geo_path = './src/eda/hangjeongdong_서울특별시.geojson'

with open(geo_path, 'r', encoding='utf-8') as f:
    geo_dong = json.load(f)

# adm_nm에서 동 이름만 추출 → dong_name 속성 추가
for feature in geo_dong['features']:
    feature['properties']['dong_name'] = feature['properties']['adm_nm'].split()[-1]



df_density['density_quantile'] = pd.qcut(df_density['점포밀도'], 5, labels=False)

fig = px.choropleth(
    df_density,
    geojson=geo_dong,
    featureidkey='properties.dong_name',
    locations='동',
    color='density_quantile',        # 분위수 컬럼 사용
    color_continuous_scale='Reds',
    hover_data=['구', '상권명', '점포밀도'],
    title='서울 동별 상권 점포 밀도 (분위수 구간)'
)

fig.update_geos(fitbounds="locations", visible=False)
fig.update_layout(height=800)
fig.show()

## 매출 기본 정보 분석

#### 2024년도 기준 총 매출 분석 - 구단위

In [17]:
import pandas as pd
import plotly.express as px

# CSV 파일 경로
csv_path = './src/eda/total_sales_gu.csv'

# 데이터 불러오기
df_gu = pd.read_csv(csv_path)

# 1. Bar Chart
fig_bar = px.bar(
    df_gu,
    x='구',
    y='총매출',
    text='총매출',
    title='2024년 4분기 구 단위 총매출',
    labels={'총매출': '총매출(원)'}
)
fig_bar.update_traces(texttemplate='%{text:,.0f}', textposition='outside')
fig_bar.update_layout(xaxis_tickangle=-45)
fig_bar.show()

# 2. Choropleth Map
# geojson 파일 필요 (서울 구 단위 geojson)
geojson_path = './src/eda/seoul_gu.geojson'
import json
with open(geojson_path, 'r', encoding='utf-8') as f:
    seoul_geo = json.load(f)

fig_map = px.choropleth(
    df_gu,
    geojson=seoul_geo,
    locations='구',
    featureidkey='properties.adm_nm',  # geojson에서 구 이름 컬럼
    color='총매출',
    color_continuous_scale='Reds',
    title='2024년도 구 단위 총매출 지도'
)
fig_map.update_geos(fitbounds="locations", visible=False)
fig_map.show()

FileNotFoundError: [Errno 2] No such file or directory: './src/eda/total_sales_gu.csv'